In [ ]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline
%cd DeepLearning_Financial

## EXTERNAL
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import sklearn
import yfinance
from pandas import Series
from sklearn.preprocessing import PolynomialFeatures, StandardScaler, MinMaxScaler
from sklearn.pipeline import Pipeline
from sklearn.model_selection import TimeSeriesSplit, PredefinedSplit
from sklearn.metrics import make_scorer
from sklearn.model_selection import cross_validate
from sklearn.model_selection import GridSearchCV
from IPython.display import display
import datetime
import torch
import torch.nn as nn
from torch.autograd import Variable
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
import torch.nn.functional as F
import numpy as np
import time
import os
import random 
from sklearn.datasets import make_regression
from torch import nn
import torch.nn.functional as F
from skorch import NeuralNetRegressor
from torch.nn.modules.loss import MSELoss
import tensorflow as tf
from tensorflow import keras
from skorch.dataset import CVSplit
from skorch import callbacks
import pickle
from sklearn.model_selection import train_test_split
from functools import partial
import skorch
import pywt
from sklearn import preprocessing
import joblib


##INTERNAL
from models import Autoencoder, waveletSmooth, SequenceDouble, SequenceDoubleAtt, SequenceAtt
from utils import prepare_data_lstm, ExampleDataset, save_checkpoint, evaluate_lstm, backtest
from testing import *
from sa_tools import *
from test_models import *



#creazione dataset
indices = ['^GSPC', '^DJI', '^HSI', '^N225', 'ASHR','^NSEI']
feature_sets = ['open', 'ohlcv', 'ext']
start_date="2000-01-01"
end_date="2018-12-31"

datasets=get_datasets(indices = indices, feature_sets = feature_sets, end_date=end_date, start_date=start_date)
tss = TimeSeriesSplit(3)#max_train_size
tss_split = CVSplit(cv=tss, stratified=False, random_state=42)

for index in indices:
    for i, (train_dates, val_dates) in enumerate(tss.split(datasets[index]["target"]), start=1):
        for model_name in get_model_names():
            
            # get the model
            save_name = "{}_{}_{}_{}.pkl".format(model_name, index, datasets[index]["target"][train_dates].index.min().date(), datasets[index]["target"][train_dates].index.max().date())
            model, feature_set = get_model(model_name,  save_name)
                
            #get the dataset
            sa=None
            ld=False
            fset= feature_set
            if(feature_set is 'ext_sa'):
                fset='ext'
                sa = "sa_{}_{}_{}".format(index, datasets[index]["target"][train_dates].index.min().date(), datasets[index]["target"][train_dates].index.max().date())
            x, y, x_train, x_val, x_scaler, y_train, y_val, y_scaler = get_dataset_train(datasets=datasets, feature_set=fset, train_dates=train_dates, val_dates=val_dates, index=index, sa=sa, ld=ld)
            
            
            #prepare dataset for training
            n_days=10

            x_batch = days_group(x, n_days=n_days)
            y_batch = y[n_days:]
            serie = x_batch
            train_dates_s = train_dates[n_days:].copy()
            val_dates_s = val_dates.copy()

            splitted = np.split(serie, [len(train_dates_s)])
            l1, l2 = len(splitted[0]), len(splitted[1])
            train_s = PredefinedSplit(np.concatenate((np.ones(l1)*-1,np.ones(l2))))
            train_split =  CVSplit(cv=train_s, stratified=False, random_state=None)  
            train_dates_s, val_dates_s = list(train_s.split(serie))[0]
            
            model.train_split = train_split
            model.fit(x_batch,y_batch)
    

[Errno 2] No such file or directory: 'DeepLearning_Financial'
/data/home/dsvm_server_admin/notebooks/fastai/tesi/DeepLearning_Financial
{'^GSPC': {'original':                Open     High      Low    Close        Volume
Date                                                        
2000-01-03  1469.25  1478.00  1438.36  1455.22  9.318000e+08
2000-01-04  1455.22  1455.22  1397.43  1399.42  1.009000e+09
2000-01-05  1399.42  1413.27  1377.68  1402.11  1.085500e+09
2000-01-06  1402.11  1411.90  1392.10  1403.45  1.092300e+09
2000-01-07  1403.45  1441.47  1400.73  1441.47  1.225200e+09
...             ...      ...      ...      ...           ...
2018-12-24  2400.56  2410.34  2351.10  2351.10  2.613930e+09
2018-12-25  2381.84  2439.05  2348.84  2409.40  3.423960e+09
2018-12-26  2363.12  2467.76  2346.58  2467.70  4.233990e+09
2018-12-27  2442.50  2489.10  2397.94  2488.83  4.096610e+09
2018-12-28  2498.77  2520.27  2472.89  2485.74  3.702620e+09

[6935 rows x 5 columns], 'features': {}, 'targe

/data/anaconda/envs/fastai/lib/python3.6/site-packages/pywt/_multilevel.py:45: UserWarning: Level value of 3 is too high: all coefficients will experience boundary effects.
  "boundary effects.").format(level))
/data/anaconda/envs/fastai/lib/python3.6/site-packages/pywt/_thresholding.py:23: RuntimeWarning: invalid value encountered in true_divide
  thresholded = (1 - value/magnitude)


Epoch 54/15000 | train loss: 6.8085 | train_error 0.1275 | valid_error 1.0146
Data Shuffled
Epoch 55/15000 | train loss: 6.8785 | train_error 0.1270 | valid_error 1.0177
Data Shuffled
Epoch 56/15000 | train loss: 6.9044 | train_error 0.1254 | valid_error 1.0094
Data Shuffled
Epoch 57/15000 | train loss: 6.9432 | train_error 0.1243 | valid_error 1.0058
Data Shuffled
Epoch 58/15000 | train loss: 6.9467 | train_error 0.1226 | valid_error 1.0024
Data Shuffled
Epoch 59/15000 | train loss: 6.9561 | train_error 0.1216 | valid_error 0.9960
Data Shuffled
Epoch 60/15000 | train loss: 6.9727 | train_error 0.1205 | valid_error 0.9930
Data Shuffled
Epoch 61/15000 | train loss: 6.9861 | train_error 0.1203 | valid_error 0.9868
Data Shuffled
Epoch 62/15000 | train loss: 7.0037 | train_error 0.1188 | valid_error 0.9912
Data Shuffled
Epoch 63/15000 | train loss: 7.0043 | train_error 0.1175 | valid_error 0.9784
Data Shuffled
Epoch 64/15000 | train loss: 7.0191 | train_error 0.1157 | valid_error 0.9822
Da

Epoch 143/15000 | train loss: 6.2036 | train_error 0.0703 | valid_error 0.8015
Data Shuffled
Epoch 144/15000 | train loss: 6.2013 | train_error 0.0700 | valid_error 0.7975
Data Shuffled
Epoch 145/15000 | train loss: 6.1795 | train_error 0.0704 | valid_error 0.7998
Data Shuffled
Epoch 146/15000 | train loss: 6.1930 | train_error 0.0690 | valid_error 0.7954
Data Shuffled
Epoch 147/15000 | train loss: 6.1809 | train_error 0.0700 | valid_error 0.8001
Data Shuffled
Epoch 148/15000 | train loss: 6.1709 | train_error 0.0688 | valid_error 0.7914
Data Shuffled
Epoch 149/15000 | train loss: 6.1493 | train_error 0.0684 | valid_error 0.7889
Data Shuffled
Epoch 150/15000 | train loss: 6.1726 | train_error 0.0684 | valid_error 0.7898
Data Shuffled
Epoch 151/15000 | train loss: 6.1700 | train_error 0.0683 | valid_error 0.7867
Data Shuffled
Epoch 152/15000 | train loss: 6.1418 | train_error 0.0680 | valid_error 0.7885
Data Shuffled
Epoch 153/15000 | train loss: 6.1490 | train_error 0.0679 | valid_erro

Epoch 233/15000 | train loss: 5.8719 | train_error 0.0577 | valid_error 0.7000
Data Shuffled
Epoch 234/15000 | train loss: 5.8584 | train_error 0.0577 | valid_error 0.7028
Data Shuffled
Epoch 235/15000 | train loss: 5.8611 | train_error 0.0581 | valid_error 0.6987
Data Shuffled
Epoch 236/15000 | train loss: 5.8552 | train_error 0.0577 | valid_error 0.6981
Data Shuffled
Epoch 237/15000 | train loss: 5.8492 | train_error 0.0575 | valid_error 0.6969
Data Shuffled
Epoch 238/15000 | train loss: 5.8413 | train_error 0.0576 | valid_error 0.6999
Data Shuffled
Epoch 239/15000 | train loss: 5.8568 | train_error 0.0571 | valid_error 0.6965
Data Shuffled
Epoch 240/15000 | train loss: 5.8322 | train_error 0.0574 | valid_error 0.7008
Data Shuffled
Epoch 241/15000 | train loss: 5.8278 | train_error 0.0569 | valid_error 0.6959
Data Shuffled
Epoch 242/15000 | train loss: 5.8244 | train_error 0.0577 | valid_error 0.6928
Data Shuffled
Epoch 243/15000 | train loss: 5.8422 | train_error 0.0571 | valid_erro

...

    685                    -0.3857  0.8518        0.0449        0.2333     +  5.1794


/data/anaconda/envs/fastai/lib/python3.6/site-packages/torch/storage.py:34: FutureWarning: pickle support for Storage will be removed in 1.5. Use `torch.save` instead
  warnings.warn("pickle support for Storage will be removed in 1.5. Use `torch.save` instead", FutureWarning)


    686                    -0.3817  0.8547        0.0447        0.2289     +  4.4092


/data/anaconda/envs/fastai/lib/python3.6/site-packages/torch/storage.py:34: FutureWarning: pickle support for Storage will be removed in 1.5. Use `torch.save` instead
  warnings.warn("pickle support for Storage will be removed in 1.5. Use `torch.save` instead", FutureWarning)


    687                    -0.3778  0.8574        0.0444        0.2246     +  8.3594
